# Imports

In [2]:
from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.neural_network import MLPClassifier
from sklearn import datasets, svm, tree, metrics
from sklearn.cluster import KMeans
from sklearn import preprocessing
import matplotlib.pyplot as plt
from pandas import DataFrame
from pathlib import Path
import collections
import numpy as np
import subprocess
import itertools
import os.path
import random
import time
import json
import sys
import re
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from nltk.tokenize import word_tokenize
import nltk

# Load Data

In [3]:
with open('input_data.json') as data:
    jdata = json.load(data)

# Clean the Data

In [4]:
def codeToList(code):
    clean_string = ' '.join(code.split())
    the_list = re.split(' |\r\n',clean_string)
    return the_list

#  Function to Translate Operators to Natural Langauge 

In [5]:
def naive_word_conversion(code_string):
    
    code_string = re.sub('\>\>=', ' is reassigned after shifting right by ', code_string)
    code_string = re.sub('\<\<=', ' is reassigned after shifting left by ', code_string)
    code_string = re.sub('\<\<', ' is shifted left by ', code_string)
    code_string = re.sub('\>\>', ' is shifted right by ' , code_string)
    code_string = re.sub('\<=', ' is less than or equal to ', code_string)
    code_string = re.sub('\>=', ' is greater than or equal to ', code_string)
    code_string = re.sub('-\>', ' is dereferenced and retrieves ', code_string)
    code_string = re.sub('\<', ' is less than ', code_string)
    code_string = re.sub('\>', ' is greater than ', code_string)
    code_string = re.sub('\+\+' ,' is incremented by one ' , code_string)
    code_string = re.sub('--', ' is decremented by one ', code_string)
    code_string = re.sub('\+=', ' is reassinged after adding ' , code_string)
    code_string = re.sub('\-=', ' is reassigned after subtracting ', code_string)
    code_string = re.sub('\*=', ' is reassigned after multiplying by ', code_string)
    code_string = re.sub('\/=', ' is reassigned after dividing by ', code_string)
    code_string = re.sub('\%=', ' is reassigned after moding by ', code_string)
    code_string = re.sub('&=', ' is reassigned after a bitwise AND of ', code_string)
    code_string = re.sub('\|=', ' is reassigned after a bitwise inclusive OR of ', code_string)
    code_string = re.sub('\^=', ' is reassigned after a bitwise exclusive OR of ', code_string)
    code_string = re.sub('==', ' is equal to ', code_string)
    code_string = re.sub('\!=', ' is not equal to ', code_string)
    code_string = re.sub('&&', ' and ', code_string)
    code_string = re.sub('\|\|', ' or ', code_string)
    code_string = re.sub('\?', ' is true then ', code_string)
    code_string = re.sub('\:', ' else is false then ', code_string)
    code_string = re.sub('\/\/', '  ', code_string)
    code_string = re.sub('=', ' equals ', code_string)
    code_string = re.sub('\.', ' uses ', code_string)
    code_string = re.sub(' -{1} ', ' is subtracted from ', code_string)
    code_string = re.sub('\+{1}', ' is added to ', code_string)
    code_string = re.sub('\/\*([^\*]|(\*+([^\*\/])))*\*\/', ' ', code_string)  
    code_string = re.sub('\*{1}', ' is multiplied by ', code_string)
    code_string = re.sub('&{1}', ' has an AND done with ', code_string)
    code_string = re.sub('\/{1}', ' is divided by ', code_string)
    code_string = re.sub('\%{1}', ' is moded by ', code_string)
    code_string = re.sub('\!{1}', ' is negated ', code_string)
    code_string = re.sub('\|{1}', ' has an OR done with ', code_string)
    code_string = re.sub('\^{1}', ' has an X OR done with ', code_string)
    code_string = re.sub('\(', ' open parenthesis ', code_string)
    code_string = re.sub('\)', ' close parenthesis ', code_string)
    code_string = re.sub('\[', ' open bracket ', code_string)
    code_string = re.sub('\]', ' close bracket ', code_string)
    code_string = re.sub('\#', ' ', code_string)
    code_string = re.sub(';', ' . ', code_string)
    
    return code_string

# Extract the Vectors 

In [6]:
samples = []
labels = []
index = []
for problem in jdata:
    for submissions in problem['Submissions']:
        for submission in submissions:
            code = submissions[submission]['Code'][0]
            code = naive_word_conversion(code)
            
            samples.append( codeToList(code))
            labels.append(str(problem['contestId']) + problem['index'])
            
            index.append(submission)

#print(samples[0:10])

[['include', 'is', 'less', 'than', 'stdio', 'uses', 'h', 'is', 'greater', 'than', 'include', 'is', 'less', 'than', 'string', 'uses', 'h', 'is', 'greater', 'than', 'int', 'len', '.', 'char', 'data', 'open', 'bracket', '200', 'close', 'bracket', '.', 'int', 'main', 'open', 'parenthesis', 'close', 'parenthesis', '{', 'int', 'i,', 'cnt', 'equals', '0', '.', 'scanf', 'open', 'parenthesis', '"', 'is', 'moded', 'by', 's",', 'data', 'close', 'parenthesis', '.', 'len', 'equals', 'strlen', 'open', 'parenthesis', 'data', 'close', 'parenthesis', '.', 'for', 'open', 'parenthesis', 'i', 'equals', '0', '.', 'i', 'is', 'less', 'than', 'len', '.', 'i', 'is', 'incremented', 'by', 'one', 'close', 'parenthesis', '{', 'if', 'open', 'parenthesis', 'data', 'open', 'bracket', 'i', 'close', 'bracket', 'is', 'equal', 'to', "'o'", 'close', 'parenthesis', 'cnt', 'is', 'incremented', 'by', 'one', '.', '}', 'if', 'open', 'parenthesis', 'cnt', 'is', 'equal', 'to', '0', 'close', 'parenthesis', 'printf', 'open', 'pare

In [7]:
print(np.unique(labels))
len(np.unique(labels))

['926A' '926C' '926G' '931A' '931B' '932A' '932B' '934A' '934B' '935A'
 '935B' '935C' '937A' '937B' '938A' '938B' '939A' '939B' '940A' '940B'
 '940C' '946A' '946B' '946C' '948A' '950A' '950B' '952A' '952C' '954A'
 '954B' '955A' '957A' '959A' '960A' '961A' '961B' '962A' '962B' '964A'
 '965A' '967A' '975B' '976A' '976B' '977A' '977B' '978A' '978B' '978C'
 '979A' '980A']


52

# Load a pre-trained Model

In [8]:
%%time
import gensim.downloader as api
# text8: First 100,000,000 bytes of plain text from Wikipedia
corpus = api.load('text8')  # download the corpus and return it opened as an iterable
corpus = [s for s in corpus]

CPU times: user 1.61 s, sys: 270 ms, total: 1.88 s
Wall time: 1.89 s


In [13]:
%%time
max_epochs = 50
vec_size = 300
alpha = 0.025

model = Doc2Vec(vector_size  = vec_size, alpha = alpha, min_alpha = 0.00025, min_count = 1,dm = 1)

samplesSingleList = []
for eachList in samples+corpus: 
    str1 = ' '.join(eachList)
    samplesSingleList.append(str1)

tagged_data = [TaggedDocument(words=word_tokenize(_d.lower()), tags=[str(i)]) for i, _d in enumerate(samplesSingleList)]

# building the vocabulary 
model.build_vocab(tagged_data)

CPU times: user 1min 3s, sys: 317 ms, total: 1min 4s
Wall time: 1min 4s


In [14]:
%%time
for epoch in range(1):
    model.train(tagged_data,total_examples = model.corpus_count,epochs = model.epochs)

CPU times: user 4min 53s, sys: 937 ms, total: 4min 54s
Wall time: 1min 41s


# Train the NLP Model

In [15]:
%%time
samplesSingleList = []
for eachList in samples: 
    str1 = ' '.join(eachList)
    samplesSingleList.append(str1)

tagged_data = [TaggedDocument(words=word_tokenize(_d.lower()), tags=[str(i)]) for i, _d in enumerate(samplesSingleList)]

CPU times: user 5.88 s, sys: 13.4 ms, total: 5.9 s
Wall time: 5.9 s


In [16]:
%%time
for epoch in range(max_epochs):
    model.train(tagged_data,total_examples = model.corpus_count,epochs = model.epochs)

CPU times: user 11min 44s, sys: 5.06 s, total: 11min 49s
Wall time: 4min 8s


In [ ]:
[[str(i)] for i, _d in enumerate(samplesSingleList)]

# Create a List of Samples

In [17]:
#print(samples)

#vectorSamples = []
#for sentence in samples:
    #accumulatedVector = np.zeros(100)
    #count =0
    #for word in sentence:
        #acumulatedVector = model.wv[word] + accumulatedVector  
        #count=count+1
    
    #vectorSamples.append(acumulatedVector/count)
    
vectorSamples = [] 

for eachString in samplesSingleList:
    vectorSamples.append(model.infer_vector(eachString))
    

# Split the Data

In [18]:
samples_train, samples_test, labels_train, labels_test = train_test_split(
    vectorSamples, labels, test_size=0.33, random_state=42)


labels_train

samples_test

labels_test

samples_train


[array([ 1.1553874 ,  2.8341668 , -4.9408174 ,  0.29584202,  4.9054327 ,
         5.960496  , -0.72584033, -0.3004077 , -1.3251091 ,  1.5329483 ,
         1.4695064 ,  5.796328  ,  0.8541549 ,  1.410661  , -3.2598557 ,
        -1.3628163 ,  3.070363  ,  2.0266414 ,  1.8524259 , -3.330098  ,
         0.51440436, -2.5608947 , -2.30263   , -0.10045177,  2.2263577 ,
         4.452518  ,  0.2468197 ,  1.4485673 ,  0.7031951 ,  1.8051423 ,
         2.912445  ,  4.5994735 , -1.4622719 ,  2.1107678 , -2.3346765 ,
        -3.0261378 , -5.8372154 , -2.373604  , -0.7444944 , -1.4079136 ,
        -0.2843844 , -0.0972986 , -0.0853651 , -3.4021423 ,  0.15565763,
        -1.1766267 , -1.5349032 ,  2.9796436 ,  1.9810696 , -2.5997875 ,
         6.11149   , -0.08910278,  3.3174767 ,  1.9380746 ,  1.4412423 ,
        -3.7273252 ,  2.835436  , -6.2675877 ,  2.8415592 , -0.8525495 ,
         0.24792828,  0.54400903,  1.5976225 , -1.3306005 ,  1.6128492 ,
        -2.0293727 , -0.666843  ,  4.8497634 ,  1.7

# Create the Machine Learning Algorithms

In [19]:
svm_classifier = svm.SVC(kernel='linear',class_weight='balanced')


dt_classifier = tree.DecisionTreeClassifier(class_weight='balanced')


rf_classifier = RandomForestClassifier(n_estimators=10,class_weight='balanced')


nn_classifier = MLPClassifier(hidden_layer_sizes=(100,70),max_iter=500)



# Scoring with vectorSamples and labels

In [20]:
svm_scores = cross_val_score(svm_classifier, vectorSamples, labels, cv=5)
print('SVM scores: ' + str(svm_scores))
svm_average = sum(svm_scores)/5
print('SVM scores average: ' + str(svm_average))

dt_scores = cross_val_score(dt_classifier, vectorSamples, labels, cv=5)
print('DT scores:  ' + str(dt_scores))
dt_average = sum(dt_scores)/5
print('DT scores average: ' + str(dt_average))

rf_scores = cross_val_score(rf_classifier, vectorSamples, labels, cv=5)
print('RF scores:  ' + str(rf_scores))
rf_average = sum(rf_scores)/5
print('RF scores average: ' + str(rf_average))


nn_scores = cross_val_score(nn_classifier, vectorSamples, labels, cv=5)
print('NN scores:  ' + str(nn_scores))
nn_average = sum(nn_scores)/5
print('NN scores average: ' + str(nn_average))

SVM scores: [0.5245283  0.54150702 0.51799486 0.51308901 0.54953765]
SVM scores average: 0.5293313677225621
DT scores:  [0.23018868 0.22733078 0.20051414 0.22120419 0.24702774]
DT scores average: 0.22525310533651588
RF scores:  [0.29811321 0.30779055 0.30205656 0.28926702 0.2998679 ]
RF scores average: 0.29941904545949144
NN scores:  [0.56352201 0.53639847 0.53213368 0.53403141 0.5006605 ]
NN scores average: 0.5333492143396367


# Scoring with samples_test and labels_test

In [ ]:
svm_scores = cross_val_score(svm_classifier, samples_test, labels_test, cv=5)
print('SVM scores: ' + str(svm_scores))
svm_average = sum(svm_scores)/5
print('SVM scores average: ' + str(svm_average))

dt_scores = cross_val_score(dt_classifier, samples_test, labels_test, cv=5)
print('DT scores:  ' + str(dt_scores))
dt_average = sum(dt_scores)/5
print('DT scores average: ' + str(dt_average))

rf_scores = cross_val_score(rf_classifier, samples_test, labels_test, cv=5)
print('RF scores:  ' + str(rf_scores))
rf_average = sum(rf_scores)/5
print('RF scores average: ' + str(rf_average))

nn_scores = cross_val_score(nn_classifier, samples_test, labels_test, cv=5)
print('NN scores:  ' + str(nn_scores))
nn_average = sum(nn_scores)/5
print('NN scores average: ' + str(nn_average))

# Fit the Model

In [ ]:
svm_classifier = svm.SVC(kernel='linear',class_weight='balanced')


dt_classifier = tree.DecisionTreeClassifier(class_weight='balanced')


rf_classifier = RandomForestClassifier(n_estimators=10,class_weight='balanced')


nn_classifier = MLPClassifier(hidden_layer_sizes=(100,70),max_iter=500)

svm_classifier.fit(samples_train,labels_train)
dt_classifier.fit(samples_train,labels_train)
rf_classifier.fit(samples_train,labels_train)
nn_classifier.fit(samples_train,labels_train)

# Final Scores

In [ ]:
score = svm_classifier.score(samples_test, labels_test)
print('SVM score: ' + str(score))
score = dt_classifier.score(samples_test, labels_test)
print('DT score: ' + str(score))
score = rf_classifier.score(samples_test, labels_test)
print('RF score: ' + str(score))
score = nn_classifier.score(samples_test, labels_test)
print('NN score: ' + str(score))